# Classic CV

In [1]:
import numpy as np
import cv2

from IPython.display import Video

filename = "gettyimages-1024761106-640_adpp.mp4"

## First Attempt - Difference

To capture the car I decided to use the difference with the previous frame. For ease of detection I zeroed contours found outside of the water. This produced pretty good results, but you can see that in some cases it messes up: for example, the first car produces two contours, also there are cases of vehicles sharing a contour.

In [2]:
def place_trail(frame, centroids):
    thickness = 1
    for j,i in enumerate(centroids[-30:-10]):
        for centr in i:
            cv2.circle(frame, centr, radius=1, color=(0, 0, 255), thickness=thickness)
        if j%3==0:
            thickness = min(thickness+1, 10)

In [3]:
vs = cv2.VideoCapture(filename)
fps = vs.get(cv2.CAP_PROP_FPS)
kernel = np.ones((4,4),np.uint8)
font = cv2.FONT_HERSHEY_SIMPLEX
centroids = []
size = (int(vs.get(cv2.CAP_PROP_FRAME_WIDTH)), int(vs.get(cv2.CAP_PROP_FRAME_HEIGHT)))

out = cv2.VideoWriter('output.mp4', cv2.VideoWriter_fourcc(*'H264'), fps, size)

road_window = (120,240)

_,prev_frame = vs.read()
_,frame = vs.read()

while frame is not None:
    A = cv2.cvtColor(prev_frame, cv2.COLOR_BGR2GRAY)
    B = cv2.cvtColor(frame, cv2.COLOR_BGR2GRAY)
    prev_frame = frame.copy()
    diff_image = cv2.absdiff(B, A)
    diff_image[:road_window[0],:] = [0] 
    diff_image[road_window[1]:,:] = [0] 

    img = cv2.adaptiveThreshold(diff_image,255,cv2.ADAPTIVE_THRESH_MEAN_C, 
                               cv2.THRESH_BINARY_INV, 11, 11)
    img = cv2.dilate(img,kernel,iterations=3)

    contours, _ = cv2.findContours(img, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)

    centroids.append([])
    count = 0
    for cntr in contours:
        x,y,w,h = cv2.boundingRect(cntr)
        if (cv2.contourArea(cntr) >= 200):
            count+=1
            cv2.rectangle(frame,(x,y),(x+w,y+h),(127,200,0),2)
            centroids[-1].append((x+w//2,y+h//2))

    place_trail(frame, centroids)
    cv2.putText(frame, f"vehicles detected: {count}", (55, 15), font, 0.6, (0, 180, 0), 2)
    out.write(frame)

    _,frame = vs.read()

out.release() 
Video("output.mp4", embed=True)

## Second Attempt - Simple

After trying to improve situation with the difference approach and failing, I decided to try just taking the frame and extracting contours from it. This approach proved to be better. Here bounding boxes are a bit shakey, but they don't split midway and don't include several vehicles.

In [4]:
vs = cv2.VideoCapture(filename)
size = (int(vs.get(cv2.CAP_PROP_FRAME_WIDTH)), int(vs.get(cv2.CAP_PROP_FRAME_HEIGHT)))
fps = vs.get(cv2.CAP_PROP_FPS)
out = cv2.VideoWriter('output2.mp4',cv2.VideoWriter_fourcc(*'H264'), fps, size)

font = cv2.FONT_HERSHEY_SIMPLEX

centroids = []
road_window = (140,240)
kernel =  cv2.getStructuringElement(cv2.MORPH_CROSS, (3,3))

_, frame = vs.read()

while(frame is not None):
    only_road = cv2.cvtColor(frame[road_window[0]:road_window[1]],cv2.COLOR_BGR2GRAY)
    only_road = cv2.adaptiveThreshold(only_road,255,cv2.ADAPTIVE_THRESH_MEAN_C, 
                               cv2.THRESH_BINARY_INV, 55, 55)

    only_road = cv2.dilate(only_road, kernel, iterations = 2)
   
    contours_unprocessed, _ = cv2.findContours(only_road, cv2.RETR_EXTERNAL, cv2.CHAIN_APPROX_SIMPLE)
    cntr_check = lambda x: cv2.contourArea(x)/only_road.size > 0.0015
    contours = [cntr for cntr in contours_unprocessed if cntr_check(cntr)]


    centroids.append([])
    for cntr in contours:
        x,y,w,h = cv2.boundingRect(cntr)
        y += road_window[0]
        centroids[-1].append((x+w//2, y+h//2))
        cv2.rectangle(frame, (x,y), (x+w, y+h), (0, 255, 0), 1)
    place_trail(frame, centroids)
    
    cv2.putText(frame, f"vehicles detected: {len(contours)}", (55, 15), font, 0.6, (0, 180, 0), 2)

    out.write(frame)
    _, frame = vs.read()

out.release()

Video('output2.mp4', embed=True)